** *italicized text*SciFact Corpus** - complete execution

*   List item
*   List item



In [ ]:
!apt-get install openjdk-21-jdk-headless -y
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-21-openjdk-amd64/"

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  openjdk-21-jre-headless
Suggested packages:
  openjdk-21-demo openjdk-21-source libnss-mdns fonts-dejavu-extra fonts-ipafont-gothic
  fonts-ipafont-mincho fonts-wqy-microhei | fonts-wqy-zenhei fonts-indic
The following NEW packages will be installed:
  openjdk-21-jdk-headless openjdk-21-jre-headless
0 upgraded, 2 newly installed, 0 to remove and 49 not upgraded.
Need to get 130 MB of archives.
After this operation, 299 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 openjdk-21-jre-headless amd64 21.0.5+11-1ubuntu1~22.04 [46.8 MB]
Get:2 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 openjdk-21-jdk-headless amd64 21.0.5+11-1ubuntu1~22.04 [82.7 MB]
Fetched 130 MB in 7s (18.1 MB/s)
Selecting previously unselected package openjdk-21-jre-headless:amd64.
(Reading data

In [ ]:

!pip3 install rank_bm25
!pip3 install pyserini

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 180.2/180.2 MB 6.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 105.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 69.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 74.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 4.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 9.2 MB/s eta 0:00:00
  Created wheel for pyserini: filename=pyserini-0.43.0-py3-none-any.whl size=180322812 sha256=02f6a53fd39c8aeb1418341e10b9908b963191e53886ffc7268610408a3bd5b1
  Stored in directory: /root/.cache/pip/wheels/2d/3d/47/d72e7062c17ae9d7c1bba0cff631e3dde93ac7c0d1868b65e4
Successfully built pyserini


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os
import numpy as np
from typing import List, Dict, Tuple
from dataclasses import dataclass
import torch
from transformers import AutoModel, AutoTokenizer
from rank_bm25 import BM25Okapi
from pyserini.search.lucene import LuceneSearcher
# from pyserini.index import IndexReader
import openai

In [ ]:
@dataclass
class QOQAConfig:
    """Configuration for QOQA system"""
    # max_iterations: int = 50
    max_iterations: int = 3

    num_initial_docs: int = 5
    num_top_queries: int = 3
    initial_rephrased: int = 3
    iterations_rephrased: int = 1
    temperature: float = 1.0
    bm25_k1: float = 1.2
    bm25_b: float = 0.75
    hybrid_alpha: float = 0.1


In [ ]:
class DenseRetriever:
    """Dense retrieval using BGE embeddings"""
    def __init__(self, model_name: str = "BAAI/bge-base-en-v1.5"):
        self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        self.tokenizer = AutoTokenizer.from_pretrained(model_name)
        self.model = AutoModel.from_pretrained(model_name).to(self.device)

    def encode(self, texts: List[str], batch_size: int = 32) -> np.ndarray:
        print("encode - start- Dense Retriever done")
        embeddings = []
        for i in range(0, len(texts), batch_size):
            batch = texts[i:i + batch_size]
            batch = [f"Represent this sentence for searching relevant passages: {text}"
                     for text in batch]
            inputs = self.tokenizer(batch, padding=True, truncation=True,
                                    return_tensors="pt").to(self.device)
            with torch.no_grad():
                outputs = self.model(**inputs)
                batch_embeddings = outputs.last_hidden_state[:, 0].cpu().numpy()
                embeddings.append(batch_embeddings)
        ans = np.vstack(embeddings)
        print("encode - end -Dense Retriever done")
        # print(ans)
        return ans

In [ ]:
class SparseRetriever:
    """BM25-based sparse retrieval"""
    def __init__(self, documents: List[str]):
        self.tokenized_docs = [doc.split() for doc in documents]
        self.bm25 = BM25Okapi(self.tokenized_docs)

    def get_scores(self, query: str) -> np.ndarray:
        print("get_scores - start- SparseRetriever")
        tokenized_query = query.split()
        res = np.array(self.bm25.get_scores(tokenized_query))

        print("get_scores - end- SparseRetriever")
        print(res)
        return res



In [ ]:
from openai import OpenAI

class QOQA:
    def __init__(self, config: QOQAConfig, documents: List[str], openai_api_key: str):
        self.config = config
        self.documents = documents
        self.dense_retriever = DenseRetriever()
        self.sparse_retriever = SparseRetriever(documents)
        self.doc_embeddings = self.dense_retriever.encode(documents)
        openai.api_key = openai_api_key

    def get_hybrid_scores(self, query: str) -> np.ndarray:
        print("get__hybrid_scores - start- QOQA")
        bm25_scores = self.sparse_retriever.get_scores(query)
        # hybrid_scores = bm25_scores
        query_embedding = self.dense_retriever.encode([query])[0]
        dense_scores = np.dot(self.doc_embeddings, query_embedding)
        hybrid_scores = (self.config.hybrid_alpha * bm25_scores +
                         (1 - self.config.hybrid_alpha) * dense_scores)
        print(hybrid_scores)
        print("get__hybrid_scores - end- QOQA")
        return hybrid_scores

    def generate_rephrased_query(self, original_query: str, top_docs: List[str], query_bucket: List[Tuple[str, float]]) -> str:
        print("generate_rephrased_query - start- QOQA")
        prompt = self._create_prompt(original_query, top_docs, query_bucket)
        client = OpenAI(api_key=open_ai_key)
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=[{"role": "user", "content": prompt}],
            temperature=self.config.temperature
        )

        rephrased_query = response.choices[0].message.content.strip("[]")
        print("generate_rephrased_query - end- QOQA")
        print(rephrased_query)
        return rephrased_query

    def _create_prompt(self, original_query: str, top_docs: List[str], query_bucket: List[Tuple[str, float]]) -> str:
        print("_create_prompt - start- QOQA")
        prompt = f"My goal is to make a rephrased query to retrieve answer documents with high scores.\n"
        prompt += f"Query: {original_query}\n\n"
        prompt += f"Top-{len(top_docs)} retrieved docs:\n"
        for idx, doc in enumerate(top_docs, 1):
            prompt += f"{idx}. {doc[:200]}...\n"
        prompt += "\nExamples of rephrased queries and scores:\n"
        for query, score in query_bucket:
            prompt += f"Rephrased query: {query}\nScore: {score:.2f}\n\n"
        prompt += "Write a new rephrased query in square brackets."
        print("_create_prompt - end - QOQA")
        print(prompt)
        return prompt

    def optimize_query(self, query: str) -> str:
        print("optimize_query - start- QOQA")
        query_bucket = []
        best_query = query
        best_score = float('-inf')
        scores = self.get_hybrid_scores(query)
        top_indices = np.argsort(scores)[-self.config.num_initial_docs:]
        top_docs = [self.documents[i] for i in top_indices]
        for _ in range(self.config.initial_rephrased):
            rephrased = self.generate_rephrased_query(query, top_docs, query_bucket)
            score = np.mean(self.get_hybrid_scores(rephrased))
            query_bucket.append((rephrased, score))
            if score > best_score:
                best_score = score
                best_query = rephrased
        for _ in range(self.config.max_iterations):
            query_bucket.sort(key=lambda x: x[1])
            query_bucket = query_bucket[-self.config.num_top_queries:]
            rephrased = self.generate_rephrased_query(query, top_docs, query_bucket)
            score = np.mean(self.get_hybrid_scores(rephrased))
            query_bucket.append((rephrased, score))
            if score > best_score:
                best_score = score
                best_query = rephrased
            if len(query_bucket) > 5 and all(abs(x[1] - score) < 1e-4 for x in query_bucket[-5:]):
                break
        print("optimize_query - end- QOQA")
        print(best_query)
        return best_query



In [ ]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 13.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 16.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.6 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [ ]:
from datasets import load_dataset

In [ ]:
# Load the BEIR scifact dataset
dataset = load_dataset("beir/scifact", "corpus")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/14.0k [00:00<?, ?B/s]

scifact.py:   0%|          | 0.00/1.66k [00:00<?, ?B/s]

The repository for beir/scifact contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/beir/scifact.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N] y


corpus.jsonl.gz:   0%|          | 0.00/2.76M [00:00<?, ?B/s]

Generating corpus split: 0 examples [00:00, ? examples/s]

In [ ]:
dataset

DatasetDict({
    corpus: Dataset({
        features: ['_id', 'title', 'text'],
        num_rows: 5183
    })
})

In [ ]:
dataset_q = load_dataset("beir/scifact", "queries")

queries.jsonl.gz:   0%|          | 0.00/49.3k [00:00<?, ?B/s]

Generating queries split: 0 examples [00:00, ? examples/s]

In [ ]:
dataset_q

DatasetDict({
    queries: Dataset({
        features: ['_id', 'title', 'text'],
        num_rows: 1109
    })
})

In [ ]:
dataset_qrel = load_dataset("BeIR/scifact-qrels", split="test")

README.md:   0%|          | 0.00/14.0k [00:00<?, ?B/s]

train.tsv:   0%|          | 0.00/14.5k [00:00<?, ?B/s]

test.tsv:   0%|          | 0.00/5.39k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/919 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/339 [00:00<?, ? examples/s]

In [ ]:
dataset_qrel

Dataset({
    features: ['query-id', 'corpus-id', 'score'],
    num_rows: 339
})

In [ ]:
for qrel in dataset_qrel:
    print(qrel)
    break

{'query-id': 1, 'corpus-id': 31715818, 'score': 1}


In [ ]:
for query in dataset_q["queries"]:
    print(query)
    break

{'_id': '0', 'title': '', 'text': '0-dimensional biomaterials lack inductive properties.'}


In [ ]:
for doc in dataset["corpus"]:
  print(doc)
  break

{'_id': '4983', 'title': 'Microstructural development of human newborn cerebral white matter assessed in vivo by diffusion tensor magnetic resonance imaging.', 'text': 'Alterations of the architecture of cerebral white matter in the developing human brain can affect cortical development and result in functional disabilities. A line scan diffusion-weighted magnetic resonance imaging (MRI) sequence with diffusion tensor analysis was applied to measure the apparent diffusion coefficient, to calculate relative anisotropy, and to delineate three-dimensional fiber architecture in cerebral white matter in preterm (n = 17) and full-term infants (n = 7). To assess effects of prematurity on cerebral white matter development, early gestation preterm infants (n = 10) were studied a second time at term. In the central white matter the mean apparent diffusion coefficient at 28 wk was high, 1.8 microm2/ms, and decreased toward term to 1.2 microm2/ms. In the posterior limb of the internal capsule, the

In [ ]:
from collections import defaultdict

# Initialize a defaultdict to store query-doc pairs
qrels = defaultdict(dict)

# Iterate over the dataset and populate the dictionary
for qrel in dataset_qrel:
    qrels[qrel["query-id"]][qrel["corpus-id"]] = qrel["score"]

# Convert defaultdict back to a regular dictionary if needed
qrels = dict(qrels)

In [ ]:
qrels

{1: {31715818: 1},
 3: {14717500: 1},
 5: {13734012: 1},
 13: {1606628: 1},
 36: {5152028: 1, 11705328: 1},
 42: {18174210: 1},
 48: {13734012: 1},
 49: {5953485: 1},
 50: {12580014: 1},
 51: {45638119: 1},
 53: {45638119: 1},
 54: {49556906: 1},
 56: {4709641: 1},
 57: {4709641: 1},
 70: {5956380: 1, 4414547: 1},
 72: {6076903: 1},
 75: {4387784: 1},
 94: {1215116: 1},
 99: {18810195: 1},
 100: {4381486: 1},
 113: {6157837: 1},
 115: {33872649: 1},
 118: {6372244: 1},
 124: {4883040: 1},
 127: {21598000: 1},
 128: {8290953: 1},
 129: {27768226: 1},
 130: {27768226: 1},
 132: {7975937: 1},
 133: {38485364: 1, 6969753: 1, 17934082: 1, 16280642: 1, 12640810: 1},
 137: {26016929: 1},
 141: {6955746: 1, 14437255: 1},
 142: {10582939: 1},
 143: {10582939: 1},
 146: {10582939: 1},
 148: {1084345: 1},
 163: {18872233: 1},
 171: {12670680: 1},
 179: {16322674: 1, 27123743: 1, 23557241: 1, 17450673: 1},
 180: {16966326: 1},
 183: {12827098: 1},
 185: {18340282: 1},
 198: {2177022: 1},
 208: {13

In [ ]:
queries = {query["_id"]: query["text"] for query in dataset_q["queries"]}

In [ ]:
corpus = {doc["_id"]: doc['text'] for doc in dataset["corpus"]}

In [ ]:
print(f"Corpus size: {len(corpus)}")
print(f"Number of queries: {len(queries)}")
print(f"Number of query-document pairs: {len(qrels)}")

Corpus size: 5183
Number of queries: 1109
Number of query-document pairs: 300


In [ ]:
len(corpus)

5183

In [ ]:
documents = list(corpus.values())


In [ ]:
doc_ids = list(corpus.keys())

In [ ]:
len(documents)

5183

In [ ]:
documents[2]

"ID elements are short interspersed elements (SINEs) found in high copy number in many rodent genomes. BC1 RNA, an ID-related transcript, is derived from the single copy BC1 RNA gene. The BC1 RNA gene has been shown to be a master gene for ID element amplification in rodent genomes. ID elements are dispersed through a process termed retroposition. The retroposition process involves a number of potential regulatory steps. These regulatory steps may include transcription in the appropriate tissue, transcript stability, priming of the RNA transcript for reverse transcription and integration. This study focuses on priming of the RNA transcript for reverse transcription. BC1 RNA gene transcripts are shown to be able to prime their own reverse transcription in an efficient intramolecular and site-specific fashion. This self-priming ability is a consequence of the secondary structure of the 3'-unique region. The observation that a gene actively amplified throughout rodent evolution makes a RN

In [ ]:
open_ai_key="<enter_openai_key_here"

In [ ]:
config = QOQAConfig()

In [ ]:
qoqa = QOQA(config, documents, openai_api_key=open_ai_key)

tokenizer_config.json:   0%|          | 0.00/366 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/777 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/438M [00:00<?, ?B/s]

encode - start- Dense Retriever done
encode - end -Dense Retriever done


In [ ]:
from tqdm import tqdm

In [ ]:
list(qrels.keys())[:100]

[1,
 3,
 5,
 13,
 36,
 42,
 48,
 49,
 50,
 51,
 53,
 54,
 56,
 57,
 70,
 72,
 75,
 94,
 99,
 100,
 113,
 115,
 118,
 124,
 127,
 128,
 129,
 130,
 132,
 133,
 137,
 141,
 142,
 143,
 146,
 148,
 163,
 171,
 179,
 180,
 183,
 185,
 198,
 208,
 212,
 213,
 216,
 217,
 218,
 219,
 230,
 232,
 233,
 236,
 237,
 238,
 239,
 248,
 249,
 261,
 268,
 269,
 274,
 275,
 279,
 294,
 295,
 298,
 300,
 303,
 312,
 314,
 324,
 327,
 338,
 343,
 350,
 354,
 362,
 380,
 384,
 385,
 386,
 388,
 399,
 410,
 411,
 415,
 421,
 431,
 436,
 437,
 439,
 440,
 443,
 452,
 475,
 478,
 491,
 501]

In [ ]:
queries[str(1)]

'0-dimensional biomaterials show inductive properties.'

In [ ]:
ndcg_scores_optimized = []
ndcg_scores_sparse = []
test_dict={}
test_dict_2={}
query_ids = list(qrels.keys())[:100]
for qid in tqdm(query_ids):

    # Original query retrieval
    # original_hits = model.sparse_retriever.search(queries[qid], k=10)
    # original_docs = [hit.docid for hit in original_hits]
    bm25_scores = qoqa.sparse_retriever.get_scores(queries[str(qid)])
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(bm25_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict[str(qid)]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict[str(qid)][str(passageid)]=top_n_scores[i]
    # sorted_passages = sorted(test_dict[qid].items(), key=lambda item: item[1], reverse=True)
    # test_dict[qid] = dict(sorted_passages[:10])


    # print(test_dict)

    # Calculate original NDCG@10
    # original_ndcg = calculate_ndcg(top_n_docids, filtered_qrels[str(qid)], k=10)

    # Optimize query
    optimized_query = qoqa.optimize_query(queries[str(qid)])

    # Optimized query retrieval
    # optimized_hits = model.sparse_retriever.search(optimized_query, k=10)
    # optimized_docs = [hit.docid for hit in optimized_hits]
    test_dict_2[str(qid)]={}

    opt_scores = qoqa.sparse_retriever.get_scores(optimized_query)

    # top_n_new_docids = sorted(range(len(opt_scores)), key=lambda i: opt_scores[i], reverse=True)[:10]
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(opt_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict_2[str(qid)]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict_2[str(qid)][str(passageid)]=top_n_scores[i]

    # Calculate optimized NDCG@10
    # optimized_ndcg = calculate_ndcg(top_n_new_docids, filtered_qrels[str(qid)], k=10)

    # ndcg_scores_optimized.append(optimized_ndcg)
    # ndcg_scores_sparse.append(original_ndcg)

  0%|          | 0/100 [00:00<?, ?it/s]

get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0.         0.         0.         ... 1.30684259 0.         0.        ]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0.         0.         0.         ... 1.30684259 0.         0.        ]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[112.74897766 106.00006104 103.91676331 ... 120.16507757 107.08460236
 104.58238983]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: 0-dimensional biomaterials show inductive properties.

Top-5 retrieved docs:
1. Cells in tissues can organize into a broad spectrum of structures according to their function. Drastic changes of organization, such as epithelial-mesenchymal transitions or the formation of spheroid

  1%|          | 1/100 [00:06<11:23,  6.90s/it]

get_scores - end- SparseRetriever
[69.32578293 90.98078254 91.48098722 ... 98.30332033 75.25994808
 88.26799952]
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[15.51641666 10.35458651  8.00518888 ...  9.4128713  11.57431574
 11.66817711]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[15.51641666 10.35458651  8.00518888 ...  9.4128713  11.57431574
 11.66817711]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[109.28788587 102.92543515 115.52091684 ... 107.711238   101.04701898
  99.86734872]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: 1,000 genomes project enables mapping of genetic sequence variation consisting of rare variants with larger penetrance effects than common variants.

To

  2%|▏         | 2/100 [00:11<09:04,  5.55s/it]

...

get_scores - end- SparseRetriever
[111.10448368 140.48256792 150.09827717 ... 119.05278253 124.98580622
 137.34738017]
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[15.25155711 14.68255392 11.76064469 ... 12.13731499 23.57217845
 15.84425873]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[15.25155711 14.68255392 11.76064469 ... 12.13731499 23.57217845
 15.84425873]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[125.2305619  122.70570504 107.00250337 ... 112.02472088 133.30773359
 118.20207114]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: HNF4A mutations can cause diabetes in mutant carriers by the age of 14 years

Top-5 retrieved docs:
1. CONTEXT Although acute hypoglycemia may be 

 99%|█████████▉| 99/100 [09:22<00:05,  5.88s/it]

get_scores - end- SparseRetriever
[116.70548021  98.83250036 104.30703555 ... 101.01023646 142.62056591
 111.15209244]
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[2.91840314 4.66090328 3.28253807 ... 5.65662371 9.28278672 8.41959226]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[2.91840314 4.66090328 3.28253807 ... 5.65662371 9.28278672 8.41959226]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[107.18283915  80.58979333  81.01853854 ...  82.00520705 110.7254207
 104.57856201]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: Headaches are not correlated with cognitive impairment.

Top-5 retrieved docs:
1. CONTEXT Chronic tension-type headaches are characterized by near-daily headache

100%|██████████| 100/100 [09:28<00:00,  5.69s/it]

get_scores - end- SparseRetriever
[142.59401274 126.44284888 118.46653171 ... 117.77937041 136.42944686
 139.18715865]


In [ ]:
top_n_docids

['17930286',
 '6191684',
 '44830890',
 '42095718',
 '15984735',
 '24510595',
 '14606752',
 '24770122',
 '22995579',
 '40996863']

In [ ]:
!pip install pytrec_eval


In [ ]:
import pytrec_eval

In [ ]:
qrels

{1: {31715818: 1},
 3: {14717500: 1},
 5: {13734012: 1},
 13: {1606628: 1},
 36: {5152028: 1, 11705328: 1},
 42: {18174210: 1},
 48: {13734012: 1},
 49: {5953485: 1},
 50: {12580014: 1},
 51: {45638119: 1},
 53: {45638119: 1},
 54: {49556906: 1},
 56: {4709641: 1},
 57: {4709641: 1},
 70: {5956380: 1, 4414547: 1},
 72: {6076903: 1},
 75: {4387784: 1},
 94: {1215116: 1},
 99: {18810195: 1},
 100: {4381486: 1},
 113: {6157837: 1},
 115: {33872649: 1},
 118: {6372244: 1},
 124: {4883040: 1},
 127: {21598000: 1},
 128: {8290953: 1},
 129: {27768226: 1},
 130: {27768226: 1},
 132: {7975937: 1},
 133: {38485364: 1, 6969753: 1, 17934082: 1, 16280642: 1, 12640810: 1},
 137: {26016929: 1},
 141: {6955746: 1, 14437255: 1},
 142: {10582939: 1},
 143: {10582939: 1},
 146: {10582939: 1},
 148: {1084345: 1},
 163: {18872233: 1},
 171: {12670680: 1},
 179: {16322674: 1, 27123743: 1, 23557241: 1, 17450673: 1},
 180: {16966326: 1},
 183: {12827098: 1},
 185: {18340282: 1},
 198: {2177022: 1},
 208: {13

In [ ]:
converted_qrels = {str(k): {str(inner_k): inner_v for inner_k, inner_v in v.items()} for k, v in qrels.items()}


In [ ]:
evaluator = pytrec_eval.RelevanceEvaluator(converted_qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'1': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '3': {'P_3': 0.3333333333333333, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 1.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.6309297535714575, 'ndcg_cut_5': 0.6309297535714575, 'ndcg_cut_10': 0.6309297535714575, 'map_cut_3': 0.5, 'map_cut_5': 0.5, 'map_cut_10': 0.5}, '5': {'P_3': 0.3333333333333333, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 1.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 1.0, 'ndcg_cut_5': 1.0, 'ndcg_cut_10': 1.0, 'map_cut_3': 1.0, 'map_cut_5': 1.0, 'map_cut_10': 1.0}, '13': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '36': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_1

In [ ]:
#bm25 i=3, q=100, general

In [ ]:
# BM25 Retrieval Baseline with SciFact Dataset
scores

{'P_3': 0.20333333333333328,
 'P_5': 0.13199999999999984,
 'P_10': 0.0729999999999999,
 'ndcg_cut_3': 0.5322522857931934,
 'ndcg_cut_5': 0.5533478761884746,
 'ndcg_cut_10': 0.5715001062748365,
 'recall_3': 0.5783333333333334,
 'recall_5': 0.6283333333333334,
 'recall_10': 0.6808333333333334,
 'map_cut_3': 0.51,
 'map_cut_5': 0.522,
 'map_cut_10': 0.5296666666666667}

In [ ]:
evaluator = pytrec_eval.RelevanceEvaluator(converted_qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict_2)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'1': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '3': {'P_3': 0.3333333333333333, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 1.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 1.0, 'ndcg_cut_5': 1.0, 'ndcg_cut_10': 1.0, 'map_cut_3': 1.0, 'map_cut_5': 1.0, 'map_cut_10': 1.0}, '5': {'P_3': 0.3333333333333333, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 1.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 1.0, 'ndcg_cut_5': 1.0, 'ndcg_cut_10': 1.0, 'map_cut_3': 1.0, 'map_cut_5': 1.0, 'map_cut_10': 1.0}, '13': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '36': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.1, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.5, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0

In [ ]:
#bm25 i=3, q=100, optimized

In [ ]:
# QOQA algorithm implementation + BM25 Retrieval Baseline with SciFact Dataset
scores

{'P_3': 0.2066666666666666,
 'P_5': 0.14799999999999983,
 'P_10': 0.08599999999999987,
 'ndcg_cut_3': 0.4830717762741167,
 'ndcg_cut_5': 0.5276456934314256,
 'ndcg_cut_10': 0.5601201397064289,
 'recall_3': 0.5641666666666666,
 'recall_5': 0.6766666666666665,
 'recall_10': 0.77,
 'map_cut_3': 0.4497222222222222,
 'map_cut_5': 0.4762222222222222,
 'map_cut_10': 0.4903611111111112}

In [ ]:
# DR run with 100 qrels and i=3

In [ ]:
ndcg_scores_optimized = []
ndcg_scores_sparse = []
test_dict={}
test_dict_2={}
query_ids = list(qrels.keys())[:100]
for qid in tqdm(query_ids):
    # Original query retrieval
    # original_hits = model.sparse_retriever.search(queries[qid], k=10)
    # original_docs = [hit.docid for hit in original_hits]
    # bm25_scores = qoqa.sparse_retriever.get_scores(queries[qid])
    query_embedding = qoqa.dense_retriever.encode([queries[str(qid)]])[0]
    dense_scores = np.dot(qoqa.doc_embeddings, query_embedding)
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(dense_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    print(top_n_docids_with_indices)
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict[str(qid)]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict[str(qid)][str(passageid)]=top_n_scores[i]
    # sorted_passages = sorted(test_dict[qid].items(), key=lambda item: item[1], reverse=True)
    # test_dict[qid] = dict(sorted_passages[:10])


    # print(test_dict)

    # Calculate original NDCG@10
    # original_ndcg = calculate_ndcg(top_n_docids, filtered_qrels[str(qid)], k=10)

    # Optimize query
    optimized_query = qoqa.optimize_query(queries[str(qid)])

    # Optimized query retrieval
    # optimized_hits = model.sparse_retriever.search(optimized_query, k=10)
    # optimized_docs = [hit.docid for hit in optimized_hits]
    test_dict_2[str(qid)]={}
    # opt_scores = qoqa.sparse_retriever.get_scores(optimized_query)
    query_embedding = qoqa.dense_retriever.encode([optimized_query])[0]
    opt_dense_scores = np.dot(qoqa.doc_embeddings, query_embedding)
    # top_n_new_docids = sorted(range(len(opt_scores)), key=lambda i: opt_scores[i], reverse=True)[:10]
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(opt_dense_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict_2[str(qid)]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict_2[str(qid)][str(passageid)]=top_n_scores[i]



  0%|          | 0/100 [00:00<?, ?it/s]

encode - start- Dense Retriever done
encode - end -Dense Retriever done
[(766, 148.80093), (1373, 147.2125), (3190, 146.40784), (4564, 144.30676), (166, 142.8736), (1858, 142.83636), (2324, 142.34073), (4241, 142.2591), (2321, 140.8609), (2723, 140.70615)]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0.         0.         0.         ... 1.30684259 0.         0.        ]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[112.74897766 106.00006104 103.91676331 ... 120.16507757 107.08460236
 104.58238983]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: 0-dimensional biomaterials show inductive properties.

Top-5 retrieved docs:
1. Cells in tissues can organize into a broad spectrum of structures according to their

  1%|          | 1/100 [00:04<08:09,  4.95s/it]

generate_rephrased_query - end- QOQA
Do 0-dimensional biomaterials possess any inductive characteristics?
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0. 0. 0. ... 0. 0. 0.]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[118.16133118 109.33513641 111.91081238 ... 124.43197632 112.53977966
 111.57472229]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Do 0-dimensional biomaterials exhibit inductive properties?] 

Top-5 re-retrieved docs:
1. Induced pluripotent stem cells (iPSCs) hold promising potential for regenerative medicine but face challenges in culture, maintaining pluripotency, and inducing differentiation. 
2. Unlike synthetic materials, biological materials often stiffen when deformed, critical for the physiological function of tissues.
3. Mesenchymal stem cells (MSCs) exhibit significant variability among donors, tissue sources, and within cell populations.
4. Mesh surgeries are wid

  2%|▏         | 2/100 [00:11<09:30,  5.82s/it]

...

generate_rephrased_query - end- QOQA
Do Golli-deficient T-cells lean towards developing an anergic phenotype in the adaptive immune response when there is a rise in Ca2+ levels in the cytosol?
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[25.23423856 29.61084254 26.77577396 ... 23.58048958 27.78881661
 24.69496733]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[122.33151407 133.20934475 107.73759021 ... 122.85981135 114.49123823
 120.06948758]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
When there is an increase in cytosolic Ca2+ levels, Golli-deficient T-cells tend to differentiate into an anergic phenotype in the adaptive immune response.
encode - start- Dense Retriever done
encode - end -Dense Retriever done
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[(4883, 174.9656), (1991, 172.16614), (3193, 171.53821), (5054, 171.06519), (2170, 169.40814), (4204, 168.738

 99%|█████████▉| 99/100 [09:02<00:05,  5.27s/it]

generate_rephrased_query - end- QOQA
Is the development of diabetes by the age of 14 common among carriers with HNF4A mutations?
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[23.25951899 25.5662409  16.01037776 ... 16.08254484 30.088528
 23.15184788]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[121.25599798 119.84853998  98.97250537 ...  98.65162759 130.56836208
 115.30834122]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Can mutations in HNF4A result in diabetes for carriers as young as 14 years old?] 

Top-5 retrieved docs:
1. CONTEXT Although acute hypoglycemia may be associated with cognitive impairment in children with type 1 diabetes, no studies to date have evaluated whether hypoglycemia is a risk factor for dementia i...
2. OBJECTIVE To determine the frequency of moderate and severe hypoglycemia and to identify clinical predictors associated with its occurrence in a large populatio

100%|██████████| 100/100 [09:06<00:00,  5.47s/it]

generate_rephrased_query - end- QOQA
Is there any relationship between headaches and cognitive function?
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[3.62721106 3.94743995 2.83610597 ... 3.71073952 8.24629288 4.30983244]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[114.01540055  82.93846806  83.20726325 ...  85.13350224 110.00506447
 118.91457242]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Does cognitive impairment have a correlation with headaches?] 

Top-5 retrieved docs:
1. CONTEXT: Chronic tension-type headaches are characterized by near-daily headaches and often are difficult to manage in primary practice. Behavioral and pharmacological therapies each appear modestly ef...
2. OBJECTIVE: To investigate the frequency of depressive and anxiety disorders in patients with chronic daily headache. BACKGROUND: There is a lack of data in the literature on the extent of psychiatric co...
3.

In [ ]:
test_dict

{'1': {'4346436': 148.80093,
  '7583104': 147.2125,
  '21456232': 146.40784,
  '37437064': 144.30676,
  '927561': 142.8736,
  '10982689': 142.83636,
  '14103509': 142.34073,
  '31715818': 142.2591,
  '14082855': 140.8609,
  '17388232': 140.70615},
 '3': {'1388704': 169.29532,
  '4414547': 166.69669,
  '19058822': 165.82356,
  '2739854': 163.164,
  '10944947': 159.58925,
  '4632921': 158.86792,
  '6290112': 155.1218,
  '14464451': 154.59525,
  '8352137': 154.57196,
  '45200347': 154.1171},
 '5': {'27063470': 157.30565,
  '13734012': 154.42656,
  '11880289': 144.66794,
  '25261168': 142.6811,
  '23124332': 142.64325,
  '21550246': 141.7092,
  '11349166': 140.62653,
  '18617259': 140.00891,
  '103007': 139.34898,
  '13791044': 139.10071},
 '13': {'1263446': 170.59879,
  '4791384': 168.81735,
  '7662395': 168.27248,
  '33257464': 165.7432,
  '13791044': 164.65347,
  '28633594': 164.15195,
  '8529693': 162.92453,
  '16322674': 161.16606,
  '1606628': 160.9556,
  '17450673': 160.74304},
 '36

In [ ]:
test_dict_converted = {
    query_id: {doc_id: float(score) for doc_id, score in doc_scores.items()}
    for query_id, doc_scores in test_dict.items()
}

In [ ]:
test_dict_converted_2 = {
    query_id: {doc_id: float(score) for doc_id, score in doc_scores.items()}
    for query_id, doc_scores in test_dict_2.items()
}

In [ ]:

evaluator = pytrec_eval.RelevanceEvaluator(converted_qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict_converted)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'1': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.1, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.31546487678572877, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.125}, '3': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '5': {'P_3': 0.3333333333333333, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 1.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.6309297535714575, 'ndcg_cut_5': 0.6309297535714575, 'ndcg_cut_10': 0.6309297535714575, 'map_cut_3': 0.5, 'map_cut_5': 0.5, 'map_cut_10': 0.5}, '13': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.1, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.3010299956639812, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.1111111111111111}, '36': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.1, 'recall_3'

In [ ]:
# DR, I =3, Q=100, general

In [ ]:
Dense Retrieval Baseline with SciFact Dataset
scores

{'P_3': 0.2733333333333331,
 'P_5': 0.1879999999999997,
 'P_10': 0.10199999999999983,
 'ndcg_cut_3': 0.6923602058455417,
 'ndcg_cut_5': 0.7317056950360613,
 'ndcg_cut_10': 0.7507799406083165,
 'recall_3': 0.7301666666666666,
 'recall_5': 0.8326666666666667,
 'recall_10': 0.8859999999999999,
 'map_cut_3': 0.6665555555555557,
 'map_cut_5': 0.6928055555555557,
 'map_cut_10': 0.7017420634920637}

In [ ]:
evaluator = pytrec_eval.RelevanceEvaluator(converted_qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict_converted_2)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'1': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '3': {'P_3': 0.0, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 0.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.43067655807339306, 'ndcg_cut_10': 0.43067655807339306, 'map_cut_3': 0.0, 'map_cut_5': 0.25, 'map_cut_10': 0.25}, '5': {'P_3': 0.3333333333333333, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 1.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.6309297535714575, 'ndcg_cut_5': 0.6309297535714575, 'ndcg_cut_10': 0.6309297535714575, 'map_cut_3': 0.5, 'map_cut_5': 0.5, 'map_cut_10': 0.5}, '13': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.1, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.2890648263178879, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.1}, '36': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3

In [ ]:
# DR, I =3, Q=100, opt

In [ ]:
# QOQA algorithm implementation + Dense Retrieval Baseline with SciFact Dataset
scores

{'P_3': 0.24333333333333318,
 'P_5': 0.1719999999999998,
 'P_10': 0.09699999999999984,
 'ndcg_cut_3': 0.5944828365106878,
 'ndcg_cut_5': 0.6354557815420285,
 'ndcg_cut_10': 0.6665487439064945,
 'recall_3': 0.6481666666666667,
 'recall_5': 0.7509999999999999,
 'recall_10': 0.843,
 'map_cut_3': 0.5641666666666667,
 'map_cut_5': 0.5931666666666667,
 'map_cut_10': 0.607186507936508}